In [1]:
"""
    This is a short demo script to show some techniques for parsing data files in python.
    In this example, I will parse a feature table for an E.coli (GB: BA000007.2), basically a long list of genes
    and other bits for this specific bacteria. The file format is a bit funky--which is perfect for us as an example.
    
    From the raw data, we will create a CSV, JSON, and XML file, and then show some techniques of how to search
    reduce, map, and otherwise manipulate such data.
    
    This script does use some not-installed-by-default python libraries. I HIGHLY suggest one sets up a python virtual
    environment to get everything installed without screwing with your standard environment. I have included a
    requirements.txt file to make life pleasant for you.
    
    This is free software, released under an MIT license.
    Authorship:
    20170802 Initial release: Jonathan Golob (j-com@golob.org)
"""

import argparse     # Python's excellent command line parser
import gzip         # to open gzip files
import pandas as pd # The python data analysis library. Lovely
import re           # regular expressions
import logging      # Logging
from collections import defaultdict # A dictionary type that allows us to specify the default entry for a key
import json
from urllib import urlretrieve


In [2]:
# Grab the data file for this example from myserver
h = urlretrieve('https://golob.org/data/ecoli_ft.txt.gz')
# Decompress and open the file. 
f = gzip.open(h[0],'rU')

In [3]:
 """
        The input file format is a typical mess for biology-oriented files.
        Each entry is identified by a line starting with a >. There is only one entity in this file, an ecoli genome.
        >Feature dbj|BA000007.2|
        After that, there blocks, one per feature:
190	273	CDS
			product	thr operon leader peptide
			transl_table	11
			protein_id	dbj|BAB33424.1|
			note	similar to THRL_ECOLI gi|1786182 percent similarity 100 in 21 aa, but has 6 additional residues (Conserved in E.coli K-12)
			evidence	not_experimental
    
    Let's unpack a feature block: Each feature block starts with three columns, whitespace delimited: Start position Stop position and feature kind
        190 - 273 there is a CDS
    
    After that there are rows that START with whitespace, first column after is the detail type, after that the details.
    
    There are a LOT of approaches to this. I'm going to use regular expressions because I enjoy bad things. 
"""
    
# create regular expressions for our three line types. I like http://pythex.org to help with this step
# entity line:
#>Feature dbj|BA000007.2|
re_entity = re.compile(r'^>(?P<entityType>\w+)\s+(?P<entityDetails>.+)')

# Feature block start:
#190	273	CDS
re_featureStart = re.compile(r'^(?P<start>\d+)\s+(?P<end>\d+)\s+(?P<featureType>\w+)')

# Feature detail:
#			transl_table	11
re_featureDetail = re.compile(r'^\s+(?P<detailCategory>\w+)\s+(?P<detail>.+)')



In [4]:
"""
    Great. I will use a single loop through the file and convert into a longitudinal format (a list of lists).
    [
    [entity,entity_details, start, end, feature_type, feature_detail_category, feature_detail],
    ....
    ]

    The worst thing of this approach is how Python handles lists that grow significantly in length.
    Once the preallocated size is exceeded, python will stop, allocate a bigger list, and then copy from the former to the new.
    The way around this is to create a large empty list from the start. As we cannot know our data size before starting, we will
    just painfully accept this for now.
"""
# Initialize our variables so we don't run into 'used before assignment' issues
entity = None
entity_details = None
feature_start = None
feature_end = None
feature_type = None
feature_detail_category = None
feature_detail  = None

features = []
for line in f:
    # Most lines are detail lines, look for them first
    featureDetail_match = re_featureDetail.match(line)
    if featureDetail_match:
        feature_detail_category     = featureDetail_match.group('detailCategory')
        feature_detail              = featureDetail_match.group('detail')
        features.append([
            entity,
            entity_details,
            feature_start,
            feature_end,
            feature_type,
            feature_detail_category,
            feature_detail
        ])
        continue
    # Implict else. Now look if we're in a new feature block
    feature_match = re_featureStart.match(line)
    if feature_match:
        feature_start       = feature_match.group('start')
        feature_end         = feature_match.group('end')
        feature_type        = feature_match.group('featureType')
        continue
    # Implicit else. Now look for an entity
    entity_match = re_entity.match(line)
    if entity_match:
        entity              = entity_match.group('entityType')
        entity_details      = entity_match.group('entityDetails')
        continue
    # Implicit else the line didn't match anything. Log it
    logging.warning("Couldn't match line: \n%s" % line)


			pseudo

			pseudo

			pseudo

			pseudo

3774355	3773333

			pseudo

			pseudo



In [5]:
# As intended, we log a few funny lines that do not conform to the standard. Otherwise we got the job done

''

In [6]:
features[0]

['Feature', 'dbj|BA000007.2|', '190', '273', 'gene', 'gene', 'ECs0001']

In [7]:
    """
        Now we will convert our list-of-lists into a pandas data frame
    """
    
    feature_df = pd.DataFrame(features, columns=['entity','entity_details','start','end','feature', 'detail_category','detail'])
    

In [9]:
feature_df.columns

Index([u'entity', u'entity_details', u'start', u'end', u'feature',
       u'detail_category', u'detail'],
      dtype='object')

In [11]:
len(feature_df)

32646

In [12]:
# Pretty quick to load in 32k of feature details

In [14]:
# Now let's do some stuff with our parsed data.
"""
    How many entities are there?
    To select a column from a dataframe, one can do df['column'] or df.column (provided the name isn't a reserved word)
    each column has a further methods, like mean(), min(), max(), and in this case most useful for us, unique()
    that gives all the unique entities in that column

"""
print "There are %d entities" % len(feature_df.entity.unique())

There are 1 entities


In [18]:
"""
    How many genes are there?
    Gene features always have 'gene' detail. We will use data slicing to get only those lines:
"""

gene_features = feature_df[feature_df.detail_category=='gene']
print "There are %d gene features." % len(gene_features)


There are 5504 gene features.


In [19]:
"""
    What do these genes make (if known)?
"""
# Slice to only lines specifying a product
feature_products = feature_df[feature_df.detail_category=='product']
print "There are %d products." % len(feature_products)

There are 5488 products.


In [20]:
"""
    Let's use our unique trick to see how many UNIQUE products there are
"""
print "There are %d unique products." % len(feature_products.detail.unique())

There are 2485 unique products.


In [21]:
"""
    What about products that have multiple copies? We can use an aggregating function in pandas to quickly figure it out,
    the powerful groupby function for each column
"""
# groupby the detail, then count how many in each group. Finally select how many unique starts there are for each group
product_counts = feature_products.groupby('detail').count()['start']
# Sort so we can get the most repeated products at the top
sorted_product_counts = product_counts.sort_values(ascending=False)
print sorted_product_counts

detail
hypothetical protein                                                        1862
putative transport protein                                                    64
putative oxidoreductase                                                       46
putative enzyme                                                               38
putative transcriptional regulator                                            37
putative ATP-binding component of a transport system                          37
putative transport system permease protein                                    31
putative minor tail protein                                                   30
putative membrane protein                                                     27
putative outer membrane protein                                               23
putative transcriptional regulator LYSR-type                                  21
hypothetical membrane protein                                                 21
putative regulator   

In [22]:
"""
    Group into entity / start / ends.
    Pandas has a very powerful and fast groupby function in dataframes. One can even select multiple columns
    by which we wish to group. In this case, we will group by start and end locations.
    (I should also do this for entities, but since we only have one we can be lazy here

    We will use this tactic to make a data structure more suitable for conversion into JSON.
    We can also use the defaultdict container to make this easier as well as dictionary comprehension.

    {'entity:
        [{
            'feature':
            'start':
            'end':
            'details': {
                'detail_type': detail
            }

        },]
    }
"""

features_by_entity = defaultdict(list)
# if this is the first time we've seen an entity, make an empty list

for (entity, start, end), location_block in feature_df.groupby(['entity_details', 'start','end']):
    for feature, feature_block in location_block.groupby('feature'):
        features_by_entity[entity].append({
            'start':    start,
            'end':      end,
            'feature':  feature,
            'details':  {r.detail_category: r.detail for idx, r in feature_block.iterrows()}  # This is a python feature called dictionary comprehension
        }) 

In [23]:
# Let's look at the result (which will be a long JSON dump)
print json.dumps(features_by_entity)

{"dbj|BA000007.2|": [{"start": "1001038", "end": "1001532", "feature": "CDS", "details": {"note": "unknown", "product": "hypothetical membrane protein", "evidence": "not_experimental", "protein_id": "dbj|BAB34337.1|", "transl_table": "11"}}, {"start": "1001038", "end": "1001532", "feature": "gene", "details": {"gene": "ECs0914"}}, {"start": "1003323", "end": "1001998", "feature": "CDS", "details": {"note": "similar to YLIG_ECOLI gi|1787057 percent identity 100 in 441 aa (Conserved in E.coli K-12)", "product": "hypothetical protein", "evidence": "not_experimental", "protein_id": "dbj|BAB34338.1|", "transl_table": "11"}}, {"start": "1003323", "end": "1001998", "feature": "gene", "details": {"gene": "ECs0915"}}, {"start": "1003536", "end": "1003919", "feature": "CDS", "details": {"note": "similar to B0836_ECOLI gi|1787059 percent identity 100 in 127 aa (Conserved in E.coli K-12)", "product": "putative receptor", "evidence": "not_experimental", "protein_id": "dbj|BAB34339.1|", "transl_tabl

In [24]:
"""
    What if we want to just output our original table to csv. Pandas just does it
"""

print feature_df.to_csv(index=None)

entity,entity_details,start,end,feature,detail_category,detail
Feature,dbj|BA000007.2|,190,273,gene,gene,ECs0001
Feature,dbj|BA000007.2|,190,273,CDS,product,thr operon leader peptide
Feature,dbj|BA000007.2|,190,273,CDS,transl_table,11
Feature,dbj|BA000007.2|,190,273,CDS,protein_id,dbj|BAB33424.1|
Feature,dbj|BA000007.2|,190,273,CDS,note,"similar to THRL_ECOLI gi|1786182 percent similarity 100 in 21 aa, but has 6 additional residues (Conserved in E.coli K-12)"
Feature,dbj|BA000007.2|,190,273,CDS,evidence,not_experimental
Feature,dbj|BA000007.2|,354,2816,gene,gene,ECs0002
Feature,dbj|BA000007.2|,354,2816,CDS,product,aspartokinase I-homoserine dehydrogenase I
Feature,dbj|BA000007.2|,354,2816,CDS,transl_table,11
Feature,dbj|BA000007.2|,354,2816,CDS,protein_id,dbj|BAB33425.1|
Feature,dbj|BA000007.2|,354,2816,CDS,note,similar to THRA_ECOLI gi|1786183 percent identity 99 in 820 aa (Conserved in E.coli K-12)
Feature,dbj|BA000007.2|,354,2816,CDS,evidence,not_experimental
Feature,dbj|BA000007.2|